# ChaCha.jl: A cryptographically secure pseudorandom number generator for Julia

Adam Sealfon

Random numbers are used for a plethora of purposes in computing, including simulation, optimization, algorithms, and cryptography. For many applications it is important to have high-quality randomness, yet true randomness is very expensive to generate. In this project I implement the a cryptographically secure pseudorandom number generator (CS-PRNG) in Julia, using the ChaCha20 algorithm designed by Daniel Bernstein. Additionally, I implement a simple symmetric-key encryption scheme (a stream cipher) based on the ChaCha PRNG. As a warmup, I also implement a simple linear congruential generator. I also test these PRNGs using the short version of the U01 test suite, implemented in the Julia package RNGTest. I also compare the performance of my PRNGs to Julia's build-in (non-cryptographically-secure) MersenneTwister PRNG and to cryptographically secure randomness obtained from calls to C and to the operating system.

In [1]:
using RNGTest
import Base: srand, rand

# Linear Congruential Generator

In [44]:
type LinearCongruentialGenerator <: AbstractRNG
    lcg_m #modulus
    lcg_mod2_64
    lcg_a #multiplier
    lcg_c #increment
    lcg_s #seed / start value
    
    #LinearCongruentialGenerator() = new(2<<30,false,1103515245,12345,makeLCGseed())
    #note that 2<<x = 2^(x+1)

    LinearCongruentialGenerator() = new(0,true,6364136223846793005,1442695040888963407,makeLCGseed())
    #These default parameters are those used in MMix by Donald Knuth
end

In [45]:
#Seed LCG randomly
function makeLCGseed()
    file::IOStream
    #Is /dev/urandom appropriate for seed generation?
    file = open("/dev/urandom") 
    x = read(file,Int64)
    close(file)
    return x
end

makeLCGseed (generic function with 1 method)

In [47]:
function srand(lcg::LinearCongruentialGenerator, seed::Int64)
    lcg.lcg_s = seed
end

srand (generic function with 11 methods)

In [48]:
#Generate random Int64
function rand(l::LinearCongruentialGenerator, ::Type{Int64})
    if(l.lcg_mod2_64)
        l.lcg_s = l.lcg_s * l.lcg_a + l.lcg_c
    else
        l.lcg_s = (l.lcg_s * l.lcg_a + l.lcg_c) % l.lcg_m
    end
    #return convert(Int32, l.lcg_s)
    return l.lcg_s
end

rand (generic function with 38 methods)

In [49]:
#For comparison / testing, generate random UInt32
function rand(l::LinearCongruentialGenerator, ::Type{UInt32})
    return convert(UInt32, (rand(l,Int64) & 4294967295))
end

rand (generic function with 38 methods)

In [50]:
makeLCGseed()

-7338454672829733088

In [51]:
lrng = LinearCongruentialGenerator()

LinearCongruentialGenerator(0,true,6364136223846793005,1442695040888963407,-5776512616815264604)

In [52]:
rand(lrng,Int64)

1338174488064443939

In [53]:
#Run TestU01 test suite on LCG random number generator
lrng = LinearCongruentialGenerator()
rng = RNGTest.wrap(LinearCongruentialGenerator(), Int64)
RNGTest.smallcrushTestU01(rng)


========= Summary results of SmallCrush =========

 Version:          TestU01 1.2.3
 Generator:        
 Number of statistics:  15
 Total CPU time:   00:00:16.56
 The following tests gave p-values outside [0.001, 0.9990]:
 (eps  means a value < 1.0e-300):
 (eps1 means a value < 1.0e-15):

       Test                          p-value
 ----------------------------------------------
  3  Gap                              eps  
  4  SimpPoker                        eps  
  5  CouponCollector                  eps  
  7  WeightDistrib                    eps  
  9  HammingIndep                     eps  
 10  RandomWalk1 H                  1.1e-16
 10  RandomWalk1 M                  1.7e-13
 ----------------------------------------------
 All other tests were passed





In [12]:
#methods(rand)

In [13]:
rng = RNGTest.wrap(LinearCongruentialGenerator(), UInt32)
RNGTest.smallcrushTestU01(rng)


========= Summary results of SmallCrush =========

 Version:          TestU01 1.2.3
 Generator:        
 Number of statistics:  15
 Total CPU time:   00:00:16.17
 The following tests gave p-values outside [0.001, 0.9990]:
 (eps  means a value < 1.0e-300):
 (eps1 means a value < 1.0e-15):

       Test                          p-value
 ----------------------------------------------
  3  Gap                              eps  
  4  SimpPoker                        eps  
  5  CouponCollector                  eps  
  7  WeightDistrib                    eps  
  9  HammingIndep                     eps  
 10  RandomWalk1 H                    eps  
 10  RandomWalk1 M                   1.1e-5
 ----------------------------------------------
 All other tests were passed





# ChaCha CS-PRNG

### The code of the random number generator itself

In [2]:
function makeChaChaseed()
    file::IOStream
    #y = Array{UInt32,16}
    y = zeros(UInt32,16)
    y[1] = 0x61707865;
    y[2] = 0x3320646e;
    y[3] = 0x79622d32;
    y[4] = 0x6b206574;
    file = open("/dev/urandom") 
    for i = 5:12
        y[i] = read(file,UInt32)
    end
    close(file)
    #13 is the block counter
    y[13] = 0;
    #14, 15, 16 are nonce
    y[14] = 0;
    y[15] = 0;
    y[16] = 0;
    return y
end

makeChaChaseed (generic function with 1 method)

In [3]:
type ChaChaGenerator <: AbstractRNG
    x::Array{UInt32,1}
    z::Array{UInt32,1}
    i::Int

    ChaChaGenerator() = new(makeChaChaseed(),[],0)
    ChaChaGenerator(y) = new(copy(y),[],0)
end

In [4]:
function lcshift(x::UInt32, s::Int)
    return (x << s) | (x >> (32 - s))
end

lcshift (generic function with 1 method)

In [5]:
function chachaQuarterRound(a::UInt32, b::UInt32, c::UInt32, d::UInt32)
    a += b; d $= a; d = lcshift(d,16);
    c += d; b $= c; b = lcshift(b,12);
    a += b; d $= a; d = lcshift(d,8);
    c += d; b $= c; b = lcshift(b,7);
    return (a,b,c,d)
end

chachaQuarterRound (generic function with 1 method)

In [6]:
function chachaQuarterRound(g::ChaChaGenerator, i1::Int, i2::Int, i3::Int, i4::Int)
    (a1,a2,a3,a4) = chachaQuarterRound(g.x[i1], g.x[i2], g.x[i3], g.x[i4]);
    g.x[i1] = a1;
    g.x[i2] = a2;
    g.x[i3] = a3;
    g.x[i4] = a4;
end

chachaQuarterRound (generic function with 2 methods)

In [7]:
function chachaQuarterRound(x::Array{UInt32}, i1::Int, i2::Int, i3::Int, i4::Int)
    (a1,a2,a3,a4) = chachaQuarterRound(x[i1], x[i2], x[i3], x[i4]);
    x[i1] = a1;
    x[i2] = a2;
    x[i3] = a3;
    x[i4] = a4;
end

chachaQuarterRound (generic function with 3 methods)

In [8]:
function ChaCha20(g::ChaChaGenerator)
    y = copy(g.x)
    for i = 1:10 #Should be 1:10
        chachaQuarterRound(y, 1,5,9,13)
        chachaQuarterRound(y, 2,6,10,14)
        chachaQuarterRound(y, 3,7,11,15)
        chachaQuarterRound(y, 4,8,12,16)
        
        chachaQuarterRound(y, 1,6,11,16)
        chachaQuarterRound(y, 2,7,12,13)
        chachaQuarterRound(y, 3,8,9,14)
        chachaQuarterRound(y, 4,5,10,15)
    end
    return g.x + y
end

ChaCha20 (generic function with 1 method)

In [9]:
#Assumes a 256-bit seed, represented as an array of 8 unsigned 32-bit ints
function srand(ccg::ChaChaGenerator, seed::Array{UInt32})
    for i=1:8
        ccg.x[i+4] = seed[i];
    end
    ccg.i=0;
end

srand (generic function with 10 methods)

In [10]:
function rand(ccg::ChaChaGenerator, ::Type{UInt32})
    if ccg.i % 16 == 0
        ccg.x[13] += 1;
        ccg.z = ChaCha20(ccg);
    end
    #Otherwise already generated the appropriate randomness, just output
    outval = ccg.z[(ccg.i % 16) + 1];
    ccg.i += 1
    return outval;
end

rand (generic function with 36 methods)

### Testing the above methods. Some tests are from the scheme specifications.

In [64]:
makeChaChaseed();

In [65]:
ccR = ChaChaGenerator()
ccR.x = [0x879531e0, 0xc5ecf37d, 0x516461b1, 0xc9a62f8a,
0x44c20ef3, 0x3390af7f, 0xd9fc690b, 0x2a5f714c,
0x53372767, 0xb00a5631, 0x974c541a, 0x359e9963,
0x5c971061, 0x3d631689, 0x2098d9d6, 0x91dbd320]

16-element Array{UInt32,1}:
 0x879531e0
 0xc5ecf37d
 0x516461b1
 0xc9a62f8a
 0x44c20ef3
 0x3390af7f
 0xd9fc690b
 0x2a5f714c
 0x53372767
 0xb00a5631
 0x974c541a
 0x359e9963
 0x5c971061
 0x3d631689
 0x2098d9d6
 0x91dbd320

In [66]:
chachaQuarterRound(ccR,3,8,9,14)

0xccc07c79

In [67]:
ccR

ChaChaGenerator(UInt32[0x879531e0,0xc5ecf37d,0xbdb886dc,0xc9a62f8a,0x44c20ef3,0x3390af7f,0xd9fc690b,0xcfacafd2,0xe46bea80,0xb00a5631,0x974c541a,0x359e9963,0x5c971061,0xccc07c79,0x2098d9d6,0x91dbd320],UInt32[],0)

In [68]:
ccR = ChaChaGenerator()
ccR.x = [0x61707865, 0x3320646e, 0x79622d32, 0x6b206574,
0x03020100, 0x07060504, 0x0b0a0908, 0x0f0e0d0c,
0x13121110, 0x17161514, 0x1b1a1918, 0x1f1e1d1c,
    0x00000001, 0x09000000, 0x4a000000, 0x00000000];
ChaCha20(ccR)

16-element Array{UInt32,1}:
 0xe4e7f110
 0x15593bd1
 0x1fdd0f50
 0xc47120a3
 0xc7f4d1c7
 0x0368c033
 0x9aaa2204
 0x4e6cd4c3
 0x466482d2
 0x09aa9f07
 0x05d7c214
 0xa2028bd9
 0xd19c12b5
 0xb94e16de
 0xe883d0cb
 0x4e3c50a2

In [69]:
ccR = ChaChaGenerator([0x61707865, 0x3320646e, 0x79622d32, 0x6b206574,
0x03020100, 0x07060504, 0x0b0a0908, 0x0f0e0d0c,
0x13121110, 0x17161514, 0x1b1a1918, 0x1f1e1d1c,
    0x00000001, 0x09000000, 0x4a000000, 0x00000000]);
ChaCha20(ccR)
#ccR

16-element Array{UInt32,1}:
 0xe4e7f110
 0x15593bd1
 0x1fdd0f50
 0xc47120a3
 0xc7f4d1c7
 0x0368c033
 0x9aaa2204
 0x4e6cd4c3
 0x466482d2
 0x09aa9f07
 0x05d7c214
 0xa2028bd9
 0xd19c12b5
 0xb94e16de
 0xe883d0cb
 0x4e3c50a2

In [70]:
ccR = ChaChaGenerator()

ChaChaGenerator(UInt32[0x61707865,0x3320646e,0x79622d32,0x6b206574,0x525d4457,0xde77af19,0x05eff33b,0xb89cbf63,0x3936529e,0x9a545228,0x41ab9611,0xd593812c,0x00000000,0x00000000,0x00000000,0x00000000],UInt32[],0)

In [71]:
rand(ccR,UInt32)

0xaef22d30

In [72]:
ccR

ChaChaGenerator(UInt32[0x61707865,0x3320646e,0x79622d32,0x6b206574,0x525d4457,0xde77af19,0x05eff33b,0xb89cbf63,0x3936529e,0x9a545228,0x41ab9611,0xd593812c,0x00000001,0x00000000,0x00000000,0x00000000],UInt32[0xaef22d30,0x2bdf7f10,0x54a93c8a,0xb8bfe905,0xcfeb3829,0x638ec32b,0x64e17f0e,0x03554c68,0x814328cf,0x1956a7e5,0xd26a1da4,0xe77c29ef,0x4ca8ad28,0xe1ce6e5f,0x5645b2cd,0x34e7e2e9],1)

In [73]:
ccR = ChaChaGenerator([0x61707865, 0x3320646e, 0x79622d32, 0x6b206574,
0x03020100, 0x07060504, 0x0b0a0908, 0x0f0e0d0c,
0x13121110, 0x17161514, 0x1b1a1918, 0x1f1e1d1c,
0x00000000, 0x00000000, 0x4a000000, 0x00000000]);

In [74]:
for i=1:32
    println(hex(rand(ccR,UInt32)))
end

f3514f22
e1d91b40
6f27de2f
ed1d63b8
821f138c
e2062c3d
ecca4f7e
78cff39e
a30a3b8a
920a6072
cd7479b5
34932bed
40ba4c79
cd343ec6
4c2c21ea
b7417df0
9f74a669
410f633f
28feca22
7ec44dec
6d34d426
738cb970
3ac5e9f3
45590cc4
da6e8b39
892c831a
cdea67c1
2b7e1d90
37463f3
a11a2073
e8bcfb88
edc49139


### The TestU01 test suite applied to ChaCha

In [11]:
rng = RNGTest.wrap(ChaChaGenerator(), UInt32)
RNGTest.smallcrushTestU01(rng)


========= Summary results of SmallCrush =========

 Version:          TestU01 1.2.3
 Generator:        
 Number of statistics:  15
 Total CPU time:   00:00:22.48

 All tests were passed





# Encryption from the ChaCha CS-PRNG

The ChaCha CS-PRNG immediately yields a simple encryption protocol. Essentially, since the PRNG produces an unpredictable sequence of numbers, this can be used as a one-time pad to mask a message, yielding a stream cipher.

### Encryption scheme

In [35]:
function KeyGen()
    g = ChaChaGenerator()
    return g.x
end

KeyGen (generic function with 1 method)

In [36]:
function Encrypt(k::Array{UInt32,1}, s::AbstractString)
    ct = zeros(UInt32,length(s));
    g = ChaChaGenerator(k);
    for i in 1:length(s)
        ct[i] = rand(g,UInt32) $ convert(UInt32,Int(s[i]));
    end
    return ct
end

Encrypt (generic function with 1 method)

In [37]:
function Decrypt(k::Array{UInt32,1}, ct::Array{UInt32,1})
    pt = zeros(UInt32,length(ct));
    g = ChaChaGenerator(k);
    for i in 1:length(ct)
        pt[i] = rand(g,UInt32) $ ct[i];
    end
    #pt2 = [Char(x) for x in pt]
    return convert(UTF32String,pt)
end

Decrypt (generic function with 1 method)

### Encryption example

In [38]:
key = KeyGen()

16-element Array{UInt32,1}:
 0x61707865
 0x3320646e
 0x79622d32
 0x6b206574
 0x3db34290
 0xac5a4dc6
 0x020d72d2
 0xdbae9c7f
 0xe0035d52
 0x31269f7c
 0x68d09068
 0x01766490
 0x00000000
 0x00000000
 0x00000000
 0x00000000

In [39]:
message = "\"A party without cake is just a meeting.\" --Julia Child"

"\"A party without cake is just a meeting.\" --Julia Child"

In [40]:
ct = Encrypt(key,message); println(ct)

UInt32[0xc14c120a,0xc15733cf,0xd574c2d0,0xa8badade,0xc78feb53,0x21210781,0x9e9bd654,0x0ff483e9,0x0b202597,0xd4c9f453,0xbddd9eb1,0x2862928a,0x435f6001,0xff793c5f,0xf5be1436,0x5ce75dfb,0xaea93bce,0x9ace0c1e,0x28913013,0x7cd59832,0x161ae3b5,0x23f29509,0x305b7478,0xd0b23174,0xa8423e9c,0xcd3c9ccc,0xea5c965d,0x9e65a4e1,0x392dbf0c,0x56fa5e32,0xd663003a,0x69384ddf,0x5fd95ba1,0x841d5ae4,0x03ebeffb,0xabb6efec,0x8ca1df7c,0x9facef79,0x963dfc27,0xc46744c9,0x0728dcc1,0xb2867b36,0xd1594b17,0xf828ce68,0x53f0917f,0xbf9a5ade,0xd6761cf2,0x96078d2f,0x5b39d128,0x86182081,0x0674f8c8,0x5db553ed,0x8becf9bc,0x9837373f,0x57d61cda]


In [41]:
pt = Decrypt(key,ct);

In [42]:
println(pt)

"A party without cake is just a meeting." --Julia Child


# Benchmarks and comparison to simple wrappers for producing random numbers

The code for my benchmarks is very messy because I was having trouble getting BenchmarkTools to work properly in loops. As a result I executed each of my tests as a separate command, which was inelegant and tedious but worked.

In [58]:
type OSWrapperCSGenerator <: AbstractRNG
end

In [48]:
function rand(ccg::OSWrapperCSGenerator, ::Type{UInt32})
    file::IOStream
    file = open("/dev/urandom") 
    x = read(file,UInt32)
    close(file)
    return x
end

rand (generic function with 38 methods)

In [49]:
using BenchmarkTools

In [50]:
ccg = ChaChaGenerator();
osg = OSWrapperCSGenerator();

In [51]:
@benchmark for i = 1:1000
    rand(ccg,UInt32)
end

BenchmarkTools.Trial: 
  samples:          10000
  evals/sample:     1
  time tolerance:   5.00%
  memory tolerance: 1.00%
  memory estimate:  111.52 kb
  allocs estimate:  6269
  minimum time:     269.33 μs (0.00% GC)
  median time:      301.00 μs (0.00% GC)
  mean time:        314.74 μs (3.34% GC)
  maximum time:     2.74 ms (86.42% GC)

In [52]:
@benchmark for i = 1:1000
    rand(osg,UInt32)
end

BenchmarkTools.Trial: 
  samples:          1
  evals/sample:     1
  time tolerance:   5.00%
  memory tolerance: 1.00%
  memory estimate:  562.50 kb
  allocs estimate:  10000
  minimum time:     6.70 s (0.00% GC)
  median time:      6.70 s (0.00% GC)
  mean time:        6.70 s (0.00% GC)
  maximum time:     6.70 s (0.00% GC)

In [53]:
ret = zeros(UInt8, 5)
ccall((:RAND_bytes, "libcrypto"), Void, (Ptr{UInt8}, Int), ret, 5)
ret

5-element Array{UInt8,1}:
 0x8d
 0x0d
 0xd5
 0x98
 0xac

In [54]:
ret = zeros(UInt8, 4)
ccall((:RAND_bytes, "libcrypto"), Void, (Ptr{UInt8}, Int), ret, 4)


In [55]:
type CWrapperCSGenerator <: AbstractRNG
end

In [56]:
function rand(cwg::CWrapperCSGenerator, ::Type{UInt32})
    ret = zeros(UInt8, 4)
    ccall((:RAND_bytes, "libcrypto"), Void, (Ptr{UInt8}, Int), ret, 4)
    return reinterpret(UInt32, ret)[1]
end

rand (generic function with 39 methods)

In [57]:
cwg = CWrapperCSGenerator();

In [58]:
@benchmark for i = 1:1000
    rand(cwg,UInt32)
end

BenchmarkTools.Trial: 
  samples:          3016
  evals/sample:     1
  time tolerance:   5.00%
  memory tolerance: 1.00%
  memory estimate:  234.38 kb
  allocs estimate:  7000
  minimum time:     1.54 ms (0.00% GC)
  median time:      1.61 ms (0.00% GC)
  mean time:        1.66 ms (1.78% GC)
  maximum time:     4.90 ms (63.03% GC)

In [62]:
Ts = [@benchmark (for j = 1:3
        rand(cwg,UInt32)
    end)
for i = 1:2]

2-element Array{Any,1}:
 Trial(5.34 μs)
 Trial(4.77 μs)

In [65]:
Ts[2]

BenchmarkTools.Trial: 
  samples:          10000
  evals/sample:     7
  time tolerance:   5.00%
  memory tolerance: 1.00%
  memory estimate:  720.00 bytes
  allocs estimate:  21
  minimum time:     4.77 μs (0.00% GC)
  median time:      5.03 μs (0.00% GC)
  mean time:        5.29 μs (1.77% GC)
  maximum time:     476.18 μs (98.06% GC)

In [64]:
[median(t) for t in Ts]

2-element Array{Any,1}:
 TrialEstimate(5.51 μs)
 TrialEstimate(5.03 μs)

In [67]:
function runTest(g::AbstractRNG, trials::Int)
    for i in 1:trials
        rand(g,UInt32)
    end
end

runTest (generic function with 1 method)

In [107]:
mtg = MersenneTwister()
lcg = LinearCongruentialGenerator()
ccg = ChaChaGenerator()
owg = OSWrapperCSGenerator()
cwg = CWrapperCSGenerator()

CWrapperCSGenerator()

@benchmark runTest(mtg,10)

In [95]:
function generateList(g::AbstractRNG)
    medtimes = []
    push!(medtimes,@benchmark runTest(g, 100))
    push!(medtimes,@benchmark runTest(g, 200))
    push!(medtimes,@benchmark runTest(g, 300))
    push!(medtimes,@benchmark runTest(g, 400))
    push!(medtimes,@benchmark runTest(g, 500))
    push!(medtimes,@benchmark runTest(g, 600))
    push!(medtimes,@benchmark runTest(g, 700))
    push!(medtimes,@benchmark runTest(g, 800))
    push!(medtimes,@benchmark runTest(g, 900))
    push!(medtimes,@benchmark runTest(g, 1000))
    return medtimes
end


generateList (generic function with 1 method)

In [86]:
medtimes = [];
for i = 1:10
    (T = @benchmark runTest(mtg, 100*i));
    push!(medtimes, median(T));
    #push!(medtimes,1)
end
mtL = medtimes;

LoadError: LoadError: UndefVarError: i not defined
while loading In[86], in expression starting on line 2

In [89]:
medtimes = [];
g = mtg;
push!(medtimes,@benchmark runTest(g, 100));
mtL = medtimes;

In [88]:
mtL

1-element Array{Any,1}:
 Trial(307.00 ns)

In [98]:
mtL = generateList(mtg)

10-element Array{Any,1}:
 Trial(307.00 ns)
 Trial(608.00 ns)
 Trial(922.00 ns)
 Trial(1.20 μs)  
 Trial(1.52 μs)  
 Trial(1.80 μs)  
 Trial(2.10 μs)  
 Trial(2.42 μs)  
 Trial(2.58 μs)  
 Trial(2.98 μs)  

In [99]:
lcL = generateList(lcg)

10-element Array{Any,1}:
 Trial(334.00 ns)
 Trial(649.00 ns)
 Trial(932.00 ns)
 Trial(1.22 μs)  
 Trial(1.55 μs)  
 Trial(1.84 μs)  
 Trial(2.15 μs)  
 Trial(2.43 μs)  
 Trial(2.55 μs)  
 Trial(2.82 μs)  

In [100]:
ccL = generateList(ccg)

10-element Array{Any,1}:
 Trial(334.00 ns)
 Trial(634.00 ns)
 Trial(932.00 ns)
 Trial(1.23 μs)  
 Trial(1.55 μs)  
 Trial(1.85 μs)  
 Trial(2.16 μs)  
 Trial(2.45 μs)  
 Trial(2.74 μs)  
 Trial(2.96 μs)  

In [101]:
cwL = generateList(cwg)

10-element Array{Any,1}:
 Trial(307.00 ns)
 Trial(603.00 ns)
 Trial(928.00 ns)
 Trial(1.15 μs)  
 Trial(1.44 μs)  
 Trial(1.80 μs)  
 Trial(2.15 μs)  
 Trial(2.43 μs)  
 Trial(2.56 μs)  
 Trial(2.81 μs)  

In [102]:
owL = generateList(owg)

10-element Array{Any,1}:
 Trial(308.00 ns)
 Trial(605.00 ns)
 Trial(929.00 ns)
 Trial(1.21 μs)  
 Trial(1.51 μs)  
 Trial(1.79 μs)  
 Trial(2.12 μs)  
 Trial(2.38 μs)  
 Trial(2.71 μs)  
 Trial(3.05 μs)  

In [106]:
median(@benchmark runTest(owg,1000))

BenchmarkTools.TrialEstimate: 
  time:             6.71 s
  gctime:           0.00 ns (0.00%)
  memory:           546.88 kb
  allocs:           9000
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [105]:
owL[10]

BenchmarkTools.Trial: 
  samples:          10000
  evals/sample:     8
  time tolerance:   5.00%
  memory tolerance: 1.00%
  memory estimate:  0.00 bytes
  allocs estimate:  0
  minimum time:     3.05 μs (0.00% GC)
  median time:      3.22 μs (0.00% GC)
  mean time:        3.25 μs (0.00% GC)
  maximum time:     5.39 μs (0.00% GC)

In [108]:
median(@benchmark runTest(mtg,100))

BenchmarkTools.TrialEstimate: 
  time:             336.00 ns
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [109]:
median(@benchmark runTest(mtg,200))

BenchmarkTools.TrialEstimate: 
  time:             662.00 ns
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [110]:
median(@benchmark runTest(mtg,300))

BenchmarkTools.TrialEstimate: 
  time:             991.00 ns
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [111]:
median(@benchmark runTest(mtg,400))

BenchmarkTools.TrialEstimate: 
  time:             1.33 μs
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [112]:
median(@benchmark runTest(mtg,500))

BenchmarkTools.TrialEstimate: 
  time:             1.63 μs
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [113]:
median(@benchmark runTest(mtg,600))

BenchmarkTools.TrialEstimate: 
  time:             1.95 μs
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [114]:
median(@benchmark runTest(mtg,700))

BenchmarkTools.TrialEstimate: 
  time:             2.27 μs
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [115]:
median(@benchmark runTest(mtg,800))

BenchmarkTools.TrialEstimate: 
  time:             2.66 μs
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [116]:
median(@benchmark runTest(mtg,900))

BenchmarkTools.TrialEstimate: 
  time:             2.93 μs
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [117]:
median(@benchmark runTest(mtg,1000))

BenchmarkTools.TrialEstimate: 
  time:             3.19 μs
  gctime:           0.00 ns (0.00%)
  memory:           0.00 bytes
  allocs:           0
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [119]:
mtTimes = [.33600,
.66200 ,
.99100 ,
1.33 ,
1.63 ,
1.95 ,
2.27 ,
2.66 ,
2.93 ,
3.19 ]
#Times in microseconds

10-element Array{Float64,1}:
 0.336
 0.662
 0.991
 1.33 
 1.63 
 1.95 
 2.27 
 2.66 
 2.93 
 3.19 

In [122]:
median(@benchmark runTest(lcg,100))

BenchmarkTools.TrialEstimate: 
  time:             22.66 μs
  gctime:           0.00 ns (0.00%)
  memory:           6.25 kb
  allocs:           400
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [123]:
median(@benchmark runTest(lcg,200))

BenchmarkTools.TrialEstimate: 
  time:             44.78 μs
  gctime:           0.00 ns (0.00%)
  memory:           12.50 kb
  allocs:           800
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [124]:
median(@benchmark runTest(ccg,100))

BenchmarkTools.TrialEstimate: 
  time:             26.69 μs
  gctime:           0.00 ns (0.00%)
  memory:           10.83 kb
  allocs:           609
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [126]:
median(@benchmark runTest(ccg,200))

BenchmarkTools.TrialEstimate: 
  time:             53.17 μs
  gctime:           0.00 ns (0.00%)
  memory:           21.67 kb
  allocs:           1219
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [127]:
median(@benchmark runTest(ccg,300))

BenchmarkTools.TrialEstimate: 
  time:             79.12 μs
  gctime:           0.00 ns (0.00%)
  memory:           32.53 kb
  allocs:           1830
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [128]:
median(@benchmark runTest(ccg,400))

BenchmarkTools.TrialEstimate: 
  time:             104.74 μs
  gctime:           0.00 ns (0.00%)
  memory:           44.89 kb
  allocs:           2523
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [129]:
median(@benchmark runTest(ccg,500))

BenchmarkTools.TrialEstimate: 
  time:             131.34 μs
  gctime:           0.00 ns (0.00%)
  memory:           55.75 kb
  allocs:           3134
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [130]:
median(@benchmark runTest(ccg,600))

BenchmarkTools.TrialEstimate: 
  time:             159.72 μs
  gctime:           0.00 ns (0.00%)
  memory:           66.59 kb
  allocs:           3744
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [131]:
median(@benchmark runTest(ccg,700))

BenchmarkTools.TrialEstimate: 
  time:             188.77 μs
  gctime:           0.00 ns (0.00%)
  memory:           77.44 kb
  allocs:           4354
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [132]:
median(@benchmark runTest(ccg,800))

BenchmarkTools.TrialEstimate: 
  time:             216.37 μs
  gctime:           0.00 ns (0.00%)
  memory:           89.83 kb
  allocs:           5049
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [133]:
median(@benchmark runTest(ccg,900))

BenchmarkTools.TrialEstimate: 
  time:             245.00 μs
  gctime:           0.00 ns (0.00%)
  memory:           100.67 kb
  allocs:           5659
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [134]:
median(@benchmark runTest(ccg,1000))

BenchmarkTools.TrialEstimate: 
  time:             271.64 μs
  gctime:           0.00 ns (0.00%)
  memory:           111.52 kb
  allocs:           6269
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [135]:
ccTimes = [26.69,
53.17,
79.12,
104.74,
131.34,
159.72,
188.77,
216.37,
245.00,
271.64]

10-element Array{Float64,1}:
  26.69
  53.17
  79.12
 104.74
 131.34
 159.72
 188.77
 216.37
 245.0 
 271.64

In [136]:
median(@benchmark runTest(cwg,100))

BenchmarkTools.TrialEstimate: 
  time:             138.96 μs
  gctime:           0.00 ns (0.00%)
  memory:           21.88 kb
  allocs:           600
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [137]:
median(@benchmark runTest(cwg,200))

BenchmarkTools.TrialEstimate: 
  time:             282.23 μs
  gctime:           0.00 ns (0.00%)
  memory:           43.75 kb
  allocs:           1200
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [138]:
median(@benchmark runTest(cwg,300))

BenchmarkTools.TrialEstimate: 
  time:             436.27 μs
  gctime:           0.00 ns (0.00%)
  memory:           65.63 kb
  allocs:           1800
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [139]:
median(@benchmark runTest(cwg,400))

BenchmarkTools.TrialEstimate: 
  time:             564.73 μs
  gctime:           0.00 ns (0.00%)
  memory:           87.50 kb
  allocs:           2400
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [140]:
median(@benchmark runTest(cwg,500))

BenchmarkTools.TrialEstimate: 
  time:             701.45 μs
  gctime:           0.00 ns (0.00%)
  memory:           109.38 kb
  allocs:           3000
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [141]:
median(@benchmark runTest(cwg,600))

BenchmarkTools.TrialEstimate: 
  time:             841.43 μs
  gctime:           0.00 ns (0.00%)
  memory:           131.25 kb
  allocs:           3600
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [142]:
median(@benchmark runTest(cwg,700))

BenchmarkTools.TrialEstimate: 
  time:             982.28 μs
  gctime:           0.00 ns (0.00%)
  memory:           153.13 kb
  allocs:           4200
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [143]:
median(@benchmark runTest(cwg,800))

BenchmarkTools.TrialEstimate: 
  time:             1.13 ms
  gctime:           0.00 ns (0.00%)
  memory:           175.00 kb
  allocs:           4800
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [144]:
median(@benchmark runTest(cwg,900))

BenchmarkTools.TrialEstimate: 
  time:             1.27 ms
  gctime:           0.00 ns (0.00%)
  memory:           196.88 kb
  allocs:           5400
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [145]:
median(@benchmark runTest(cwg,1000))

BenchmarkTools.TrialEstimate: 
  time:             1.40 ms
  gctime:           0.00 ns (0.00%)
  memory:           218.75 kb
  allocs:           6000
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [146]:
cwTimes = [138.96,
282.23,
436.27,
564.73,
701.45,
841.43,
982.28,
1130,
1270,
    1400]

10-element Array{Float64,1}:
  138.96
  282.23
  436.27
  564.73
  701.45
  841.43
  982.28
 1130.0 
 1270.0 
 1400.0 

In [147]:
median(@benchmark runTest(owg,100))

BenchmarkTools.TrialEstimate: 
  time:             672.90 ms
  gctime:           0.00 ns (0.00%)
  memory:           54.69 kb
  allocs:           900
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [148]:
median(@benchmark runTest(owg,200))

BenchmarkTools.TrialEstimate: 
  time:             1.36 s
  gctime:           0.00 ns (0.00%)
  memory:           109.38 kb
  allocs:           1800
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [149]:
median(@benchmark runTest(owg,300))

BenchmarkTools.TrialEstimate: 
  time:             2.05 s
  gctime:           0.00 ns (0.00%)
  memory:           164.06 kb
  allocs:           2700
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [150]:
median(@benchmark runTest(owg,400))

BenchmarkTools.TrialEstimate: 
  time:             2.68 s
  gctime:           0.00 ns (0.00%)
  memory:           218.75 kb
  allocs:           3600
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [151]:
median(@benchmark runTest(owg,500))

BenchmarkTools.TrialEstimate: 
  time:             3.41 s
  gctime:           0.00 ns (0.00%)
  memory:           273.44 kb
  allocs:           4500
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [152]:
median(@benchmark runTest(owg,600))

BenchmarkTools.TrialEstimate: 
  time:             4.05 s
  gctime:           0.00 ns (0.00%)
  memory:           328.13 kb
  allocs:           5400
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [153]:
median(@benchmark runTest(owg,700))

BenchmarkTools.TrialEstimate: 
  time:             4.71 s
  gctime:           0.00 ns (0.00%)
  memory:           382.81 kb
  allocs:           6300
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [154]:
median(@benchmark runTest(owg,800))

BenchmarkTools.TrialEstimate: 
  time:             5.39 s
  gctime:           0.00 ns (0.00%)
  memory:           437.50 kb
  allocs:           7200
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [155]:
median(@benchmark runTest(owg,900))

BenchmarkTools.TrialEstimate: 
  time:             6.09 s
  gctime:           0.00 ns (0.00%)
  memory:           492.19 kb
  allocs:           8100
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [156]:
median(@benchmark runTest(owg,1000))

BenchmarkTools.TrialEstimate: 
  time:             6.78 s
  gctime:           0.00 ns (0.00%)
  memory:           546.88 kb
  allocs:           9000
  time tolerance:   5.00%
  memory tolerance: 1.00%

In [184]:
owTimes = [672900,
1360000,
2050000,
2680000,
3410000,
4050000,
4710000,
5390000,
6090000,
6780000]

10-element Array{Int64,1}:
  672900
 1360000
 2050000
 2680000
 3410000
 4050000
 4710000
 5390000
 6090000
 6780000

In [158]:
Pkg.add("Plots")

INFO: Cloning cache of PlotUtils from git://github.com/JuliaPlots/PlotUtils.jl.git
INFO: Cloning cache of Plots from git://github.com/tbreloff/Plots.jl.git
INFO: Cloning cache of RecipesBase from git://github.com/JuliaPlots/RecipesBase.jl.git
INFO: Installing ColorTypes v0.2.8
INFO: Installing Colors v0.6.8
INFO: Installing FixedPointNumbers v0.1.8
INFO: Installing Iterators v0.1.10
INFO: Installing Measures v0.0.3
INFO: Installing PlotUtils v0.0.4
INFO: Installing Plots v0.8.2
INFO: Installing RecipesBase v0.0.6
INFO: Installing Reexport v0.0.3
INFO: Installing Showoff v0.0.7
INFO: Building Plots
INFO: Cannot find deps/plotly-latest.min.js... downloading latest version.
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 1771k  100 1771k    0     0  5719k      0 --:--:-- --:--:-- --:--:-- 5715k
INFO: Package database updated
INFO: METADATA is out-of-date — you may not have the

In [160]:
using Plots

INFO: Precompiling module Plots.


In [178]:
plot(mtTimes, label="Mersenne twister")
plot!(ccTimes, label="ChaCha", xticks=1:10,xlabel = "Samples (x100)", ylabel = "time (microseconds)")

In [195]:
plot(ccTimes./mtTimes, label="CC/MT", xticks=1:10,xlabel = "Samples (x100)", ylabel = "Ratio of time")

In [194]:
plot(cwTimes, label="C libcrypto wrapper")
plot!(ccTimes, label="ChaCha", xticks=1:10,xlabel = "Samples (x100)", ylabel = "time (microseconds)")

In [193]:
plot(cwTimes, label="C libcrypto wrapper")
plot!(owTimes/1000, label="OS wrapper / 1000")
plot!(ccTimes, label="ChaCha", xticks=1:10,xlabel = "Samples (x100)", ylabel = "time (microseconds)")

In [189]:
plot(cwTimes ./ ccTimes, label="libcrypto / ChaCha", xticks=1:10,xlabel = "Samples (x100)", ylabel = "Ratio of time")

In [191]:
plot(owTimes ./ ccTimes, label="System call / ChaCha", xticks=1:10,xlabel = "Samples (x100)", ylabel = "Ratio of time")

In [197]:
median(@benchmark runTest(lcg,1000))

BenchmarkTools.TrialEstimate: 
  time:             218.68 μs
  gctime:           0.00 ns (0.00%)
  memory:           62.47 kb
  allocs:           3998
  time tolerance:   5.00%
  memory tolerance: 1.00%